In [ ]:
from pathlib import Path
from typing import Dict, List
from tqdm import tqdm

import pandas as pd
import srsly
import spacy
from spacy.training.iob_utils import biluo_to_iob
from spacy.training import offsets_to_biluo_tags


In [ ]:
dataset_path = Path("promises-elections-pl-twitter-1-reviewed-fixed-case.jsonl")

In [ ]:
data = list(srsly.read_jsonl(dataset_path.as_posix()))

In [ ]:
import uuid
from IPython.display import display_javascript, display_html
import json

class RenderJSON(object):
    def __init__(self, json_data):
        if isinstance(json_data, dict):
            self.json_str = json.dumps(json_data)
        else:
            self.json_str = json
        self.uuid = str(uuid.uuid4())
        
    def _ipython_display_(self):
        display_html('<div id="{}" style="height: 600px; width:100%;"></div>'.format(self.uuid),
            raw=True
        )
        display_javascript("""
        require(["https://rawgit.com/caldwell/renderjson/master/renderjson.js"], function() {
          document.getElementById('%s').appendChild(renderjson(%s))
        });
        """ % (self.uuid, self.json_str), raw=True)

In [ ]:
RenderJSON(data[0])

In [ ]:
data_df = pd.DataFrame(data)

In [ ]:
data[0]["text"]

In [ ]:
data_df = data_df[data_df.answer == "accept"]

In [ ]:
data_df.text[1]

In [ ]:
data_df.text[1][202:224]

In [ ]:
data_df.spans[1]

In [ ]:
def convert_spacy_to_iob(text: str, spans: List[Dict], nlp: spacy.language.Language) -> str:
    doc = nlp(text)
    entities = [(span["start"], span["end"], span["label"].upper()) for span in spans]
    if entities:
        main_entity = list(set(span["label"].upper() for span in spans))[0]
    else:
        main_entity = None
    tags = offsets_to_biluo_tags(doc, entities)
    # then convert L->I and U->B to have IOB tags for the tokens in the doc
    # tags_corrected = [tag.replace("L-", "I-").replace("U-", "B-") for tag in tags]
    tags_corrected = biluo_to_iob(tags)
    tokens = [token.text for token in doc]
    return {
        "tokens": tokens, 
        "tags": tags_corrected,
        "label": main_entity or ""
    }

In [ ]:
from spacy.lang import pl

nlp = pl.Language()

In [ ]:
from pprint import pprint

In [ ]:
tokens, tags, label = convert_spacy_to_iob(data_df.text[0], data_df.spans[0], nlp)

In [ ]:
tokens

In [ ]:
tags

In [ ]:
label

In [ ]:
iob_dataset = pd.DataFrame([
    {
        **convert_spacy_to_iob(row["text"], row["spans"], nlp),
        # "url": row["url"],
        # "tweet_id": row["url"].split("/")[-1],
    }
    for _, row
    in tqdm(data_df.iterrows())
])

In [ ]:
iob_dataset

In [ ]:
iob_dataset.label.value_counts()

In [ ]:
from more_itertools import flatten 

In [ ]:
sorted(set(flatten(iob_dataset.tags)))

In [ ]:
from sklearn.model_selection import train_test_split

In [ ]:
train, test = train_test_split(iob_dataset, test_size=0.4)
dev, test = train_test_split(test, test_size=0.5)

In [ ]:
train.label.value_counts()

In [ ]:
train.reset_index(inplace=True, drop=True)
train.drop(columns=["label"], inplace=True)

In [ ]:
train

In [ ]:
len(train)

In [ ]:
len(test)

In [ ]:
len(dev)

In [ ]:
test

In [ ]:
test.label.value_counts()

In [ ]:
test.reset_index(inplace=True, drop=True)
test.drop(columns=["label"], inplace=True)

In [ ]:
test

In [ ]:
dev

In [ ]:
dev.label.value_counts()

In [ ]:
dev.reset_index(inplace=True, drop=True)
dev.drop(columns=["label"], inplace=True)

In [ ]:
dev

In [ ]:
train.to_parquet("../train.parquet")
test.to_parquet("../test.parquet")
dev.to_parquet("../dev.parquet")

In [ ]:
df = pd.read_parquet("../train.parquet")

In [ ]:
df